In [0]:
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=email%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdocs.test%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.photos.readonly%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/drive


In [0]:
import os 
os.makedirs('/content/drive/My Drive/Csagan_pics/')
os.makedirs('/content/drive/My Drive/Csagan_models/')
os.makedirs('/content/drive/My Drive/Csagan_events_new')


In [0]:
%reload_ext tensorboard
%tensorboard --logdir '/content/drive/My Drive/Csagan_events_new'

In [0]:
# source: stackoverflow
from keras import backend as K
from keras.layers import Layer, InputSpec
import tensorflow as tf
class Attention(Layer):
    def __init__(self, ch):
        super(Attention, self).__init__()
        self.channels = ch
        self.filters_f_g = self.channels // 8
        self.filters_h = self.channels

    def build(self, input_shape):
        kernel_shape_f_g = (1, 1) + (self.channels, self.filters_f_g)
        print(kernel_shape_f_g)
        kernel_shape_h = (1, 1) + (self.channels, self.filters_h)
        # Create a trainable weight variable for this layer:
        self.gamma = self.add_weight(name='gamma', shape=[1], initializer='zeros', trainable=True)
        self.kernel_f = self.add_weight(shape=kernel_shape_f_g,initializer='glorot_uniform',name='kernel_f')
        self.kernel_g = self.add_weight(shape=kernel_shape_f_g,initializer='glorot_uniform',name='kernel_g')
        self.kernel_h = self.add_weight(shape=kernel_shape_h,initializer='glorot_uniform',name='kernel_h')
        self.bias_f = self.add_weight(shape=(self.filters_f_g,),initializer='zeros',name='bias_F')
        self.bias_g = self.add_weight(shape=(self.filters_f_g,),initializer='zeros',name='bias_g')
        self.bias_h = self.add_weight(shape=(self.filters_h,),initializer='zeros',name='bias_h')
        super(Attention, self).build(input_shape)
        # Set input spec.
        self.input_spec = InputSpec(ndim=4,axes={3: input_shape[-1]})
        self.built = True
        
    def call(self, x):
        def hw_flatten(x):
            return K.reshape(x, shape=[K.shape(x)[0], K.shape(x)[1]*K.shape(x)[2], K.shape(x)[-1]])
        f = K.conv2d(x,kernel=self.kernel_f,strides=(1, 1), padding='same')  # [bs, h, w, c']
        f = K.bias_add(f, self.bias_f)
        g = K.conv2d(x,kernel=self.kernel_g,strides=(1, 1), padding='same')  # [bs, h, w, c']
        g = K.bias_add(g, self.bias_g)
        h = K.conv2d(x,kernel=self.kernel_h,strides=(1, 1), padding='same')  # [bs, h, w, c]
        h = K.bias_add(h, self.bias_h)
        s = tf.matmul(hw_flatten(g), hw_flatten(f), transpose_b=True)  # # [bs, N, N]
        beta = K.softmax(s, axis=-1)  # attention map
        o = K.batch_dot(beta, hw_flatten(h))  # [bs, N, C]
        o = K.reshape(o, shape=K.shape(x))  # [bs, h, w, C]
        x = self.gamma * o + x
        return [x,beta]
    def compute_output_shape(self, input_shape):
        return [input_shape,(256,256)]

Using TensorFlow backend.


In [0]:
tensorboard = tf.keras.callbacks.TensorBoard(
  log_dir='/content/drive/My Drive/Csagan_events_new',
    histogram_freq=0,
    batch_size=128,
    write_graph=True,
    write_grads=True
    )


In [0]:
%matplotlib inline
# example of a dcgan on cifar10
from numpy import expand_dims
from numpy import zeros
from numpy import ones
from numpy import vstack, hstack
from keras.layers import Concatenate
from keras.layers import Input
from numpy.random import randn
from numpy.random import randint
from keras.datasets.cifar10 import load_data
from keras.optimizers import Adam
from keras.models import Sequential
from keras.layers import Dense
from keras.layers import Reshape
from keras.layers import Flatten
from keras.layers import Conv2D
from keras.layers import Conv2DTranspose
from keras.layers import LeakyReLU
from keras.layers import Dropout
from keras.layers import BatchNormalization
from matplotlib import pyplot
from keras.applications.inception_v3 import InceptionV3
from keras.applications.inception_v3 import preprocess_input
# from sagan import Attention
from sn import ConvSN2D, ConvSN2DTranspose, DenseSN  
from tensorflow.keras.callbacks import TensorBoard
import numpy
from keras.models import Model
from numpy import cov
from numpy import trace
from numpy import iscomplexobj
from numpy import asarray
from scipy.linalg import sqrtm
from skimage.transform import resize
import keras.backend as K
from keras.constraints import Constraint
from keras.initializers import RandomNormal
from keras.constraints import Constraint
from keras.optimizers import RMSprop
from numpy import mean
from numpy import ones
from keras.utils import to_categorical
# clip model weights to a given hypercube
class ClipConstraint(Constraint):
	# set clip value when initialized
	def __init__(self, clip_value):
		self.clip_value = clip_value

	# clip model weights to hypercube
	def __call__(self, weights):
		return K.clip(weights, -self.clip_value, self.clip_value)

	# get the config
	def get_config(self):
		return {'clip_value': self.clip_value}
	
def wasserstein_loss(y_true, y_pred):
	return K.mean(y_true * y_pred)


def define_discriminator(in_shape=(32,32,3),cond_shape=(10,)):
  # weight initialization
  init = RandomNormal(stddev=0.02)
  # weight constraint
  const = ClipConstraint(0.01)
  in_image = Input(shape=in_shape)
  in_label = Input(shape=cond_shape)
  fl = ConvSN2D(64, kernel_size=3, strides=1, kernel_initializer=init, kernel_constraint=const, padding='same', input_shape=(32,32,3))(in_image)
  fl = LeakyReLU(0.2)(fl)
  fl = ConvSN2D(128, kernel_size=3, strides=2,kernel_initializer=init, kernel_constraint=const, padding='same')(fl)
  fl = LeakyReLU(0.1)(fl)
  [fl, beta] = Attention(64*2)(fl)  
  fl = ConvSN2D(256, kernel_size=3, strides=2,kernel_initializer=init, kernel_constraint=const, padding='same')(fl)
  fl = LeakyReLU(0.1)(fl)
  fl = ConvSN2D(512, kernel_size=3, strides=2,kernel_initializer=init, kernel_constraint=const, padding='same')(fl)
  fl = LeakyReLU(0.1)(fl)
  x = Flatten()(fl)
  x= Concatenate()([x,in_label])
  x = DenseSN(1,kernel_initializer=init, kernel_constraint=const)(x)
  opt = RMSprop(lr=0.0004)
  model = Model([in_image,in_label],x)
  model.compile(loss=wasserstein_loss, optimizer=opt, metrics=['accuracy'])
  return model

# define the standalone generator model
def define_generator(latent_dim):
 #A guide to convolution arithmetic for deeplearningVincent Dumoulin1Fand Francesco Visin2F†FMILA, Université de Montréal†AIRLab, Politecnico di MilanoJanuary 12, 20181dumouliv@iro.umontreal.ca2francesco.visin@polimi.itarXiv:1603.07285v2  [stat.ML]  11 Jan 2018
 #https://machinelearningmastery.com/upsampling-and-transpose-convolution-layers-for-generative-adversarial-networks/
 #using stride 2 and padding 'same' for upscaling (doubling the edge size)
  init = RandomNormal(stddev=0.02)
  in_points = Input(shape=(latent_dim,))
  fl = Dense(4*4*512,  kernel_initializer=init)(in_points)
  fl = LeakyReLU(alpha=0.2)(fl)
  fl = Reshape((4,4,512))(fl)
  fl = ConvSN2DTranspose(256, kernel_size=4, strides=2, padding='same',  kernel_initializer=init)(fl)
  fl = LeakyReLU(alpha=0.2)(fl)
  fl = ConvSN2DTranspose(128, kernel_size=4, strides=2, padding='same',   kernel_initializer=init)(fl)
  fl = LeakyReLU(alpha=0.2)(fl)
  [fl, beta] = Attention(64*2)(fl)  
  fl = ConvSN2DTranspose(64,  kernel_size=4, strides=2, padding='same',  kernel_initializer=init)(fl)
  fl = LeakyReLU(alpha=0.2)(fl)
  fl = ConvSN2DTranspose(3,   kernel_size=3, strides=1, padding='same', activation='tanh',  kernel_initializer=init)(fl)
  model = Model(in_points,fl)
  return model

# define the combined generator and discriminator model, for updating the generator
def define_gan(g_model, d_model):
  d_model.trainable = False
  gen_label = Input(shape=(10,))
  # get noise and label inputs from generator model
  gen_noise = g_model.input
  # get image output from the generator model
  gen_output = g_model.output
  # connect image output and label input from generator as inputs to discriminator
  gan_output = d_model([gen_output, gen_label])
  # define gan model as taking noise and label and outputting a classification
  model = Model([gen_noise, gen_label], gan_output)

  # compile model
  opt = RMSprop(lr=0.0002)
  model.compile(loss=wasserstein_loss, optimizer=opt)
  return model


def load_real_samples():
  # load cifar10 dataset
  (trainX, trainY), (testX, testY) = load_data()
  # convert from unsigned ints to floats
  X = trainX.astype('float32')
  # scale from [0,255] to [-1,1]
  X = (X - 127.5) / 127.5
  return [X, trainY]

# select real samples
def generate_real_samples(dataset, n_samples):
  images, labels = dataset
    # choose random instances
  ix = randint(0, dataset[0].shape[0], n_samples)
  # retrieve selected images
  X = images[ix]
  labels = to_categorical(labels[ix], num_classes = 10)
  # generate 'real' class labels (1)
  y = -ones((n_samples, 1))
  return [X, labels], y

# generate points in latent space as input for the generator
def generate_latent_points(latent_dim, n_samples):
  # generate points in the latent space
  x_input = randn(latent_dim * n_samples)
  # reshape into a batch of inputs for the network
  x_input = x_input.reshape(n_samples, latent_dim)
  return x_input

# use the generator to generate n fake examples, with class labels
def generate_fake_samples(g_model, labels, latent_dim, n_samples):
  # generate points in latent space
  x_input = generate_latent_points(latent_dim, n_samples)
  x_concat = hstack((x_input, labels))
  # predict outputs
  X = g_model.predict(x_concat)
  # create 'fake' class labels (0)
  y = ones((n_samples, 1))
  return X, y

# create and save a plot of generated images
def save_plot(examples, epoch, n=8):
	print("In save_plot")
	# scale from [-1,1] to [0,1]
	examples = (examples + 1) / 2.0
	# plot images
	for i in range(n * n):
	  # define subplot
	  pyplot.subplot(n, n, 1 + i)
	  # turn off axis
	  pyplot.axis('off')
	  # plot raw pixel data
	  pyplot.imshow(examples[i])
	# save plot to file
	filename = '/content/drive/My Drive/Csagan_pics/generated_plot_e%04d.png' % (epoch+1)
	pyplot.savefig(filename)
	pyplot.close()
  
def calc_FID_score(g_model, latent_dim, n_samples=1000):  
  (_,_),(trainX, trainY) = load_data()
  
  rand_idx = randint(0, len(trainX), n_samples)
  real_samples = trainX[rand_idx]
  real_Ys = trainY[rand_idx]
  # resize images
  images1 = scale_images(real_samples, (299,299,3))  
  cond = to_categorical(real_Ys)
  fake_images, labels = generate_fake_samples(g_model, cond, latent_dim, n_samples)
  images2 = scale_images(fake_images, (299,299,3))
  
  act1 = mod.predict(images1)
  act2 = mod.predict(images2)
  # calculate mean and covariance statistics
  mu1, sigma1 = act1.mean(axis=0), np.cov(act1, rowvar=False)
  mu2, sigma2 = act2.mean(axis=0), np.cov(act2, rowvar=False)

  # calculate sum squared difference between means
  ssdiff = np.sum((mu1 - mu2)**2.0)

  # calculate sqrt of product between cov
  covmean = sqrtm(sigma1.dot(sigma2))

  # check and correct imaginary numbers from sqrt
  if np.iscomplexobj(covmean):
    covmean = covmean.real

  # calculate score
  fid = ssdiff + np.trace(sigma1 + sigma2 - 2.0 * covmean)
  print('FID SCORE:', fid)
  return fid

# generate samples and save as a plot and save the model
def summarize_performance(step, g_model,c_model ,latent_dim, n_samples=100, n=8):
	# prepare fake examples
	labels_random = randint(0,10,n_samples)
	c_labels = to_categorical(labels_random, num_classes = 10) 
	X, _ = generate_fake_samples(g_model, c_labels,latent_dim, n_samples)
	# scale from [-1,1] to [0,1]
	X = (X + 1) / 2.0
	save_plot(X, step)
	# save the generator model
	filename2 = '/content/drive/My Drive/Csagan_models/model_%04d.h5' % (step+1)
	g_model.save(filename2)
	print('>Saved: %s' % (filename2))
	filename3 = '/content/drive/My Drive/Csagan_models/discmodel_%04d.h5' % (step+1)
	c_model.save(filename3)

def train(g_model, c_model, gan_model, dataset, latent_dim, n_epochs, n_batch=128, n_critic=5):
	# calculate the number of batches per training epoch
	bat_per_epo = int(dataset[0].shape[0] / n_batch)
	# calculate the number of training iterations
	n_steps = bat_per_epo * n_epochs
	# calculate the size of half a batch of samples
	half_batch = int(n_batch / 2)
	# lists for keeping track of loss
	c1_hist, c2_hist, g_hist = list(), list(), list()
	# manually enumerate epochs
	for i in range(n_steps):
		# update the critic more than the generator
		c1_tmp, c2_tmp = list(), list()
		for _ in range(n_critic):
			# get randomly selected 'real' samples
			[X_real,real_labels] ,y_real = generate_real_samples(dataset, half_batch)
			# update critic model weights
			c_loss1 = c_model.train_on_batch([X_real,real_labels], y_real)
			c1_tmp.append(c_loss1)
			# generate 'fake' examples
			X_fake, y_fake = generate_fake_samples(g_model,real_labels ,latent_dim, half_batch)
			# update critic model weights
			c_loss2 = c_model.train_on_batch([X_fake,real_labels], y_fake)
			c2_tmp.append(c_loss2)
		# store critic loss
		c1_hist.append(mean(c1_tmp))
		c2_hist.append(mean(c2_tmp))
		# prepare points in latent space as input for the generator
		X_gan = generate_latent_points(latent_dim+10, n_batch)
		# create inverted labels for the fake samples
		y_gan = -ones((n_batch, 1))
		random_labels = randint(0,10,n_batch)
		condition_labels = to_categorical(random_labels, num_classes=10)     
		# update the generator via the critic's error
		g_loss = gan_model.train_on_batch([X_gan,condition_labels], y_gan)
		g_hist.append(g_loss)
		tensorboard.set_model(gan_model)
		tensorboard.on_epoch_end(i, {"C_real_loss":c1_hist[-1] ,"C_fake_loss":c2_hist[-1],"GAN_loss":g_loss})
		# summarize loss on this batch
		print('>%d, c1=%.3f, c2=%.3f g=%.3f' % (i+1, c1_hist[-1], c2_hist[-1], g_loss))
		# evaluate the model performance every 'epoch'
		if (i+1) % (5*bat_per_epo) == 0:
			summarize_performance(i, g_model,c_model ,latent_dim)
			calc_FID_score(g_model, latent_dim,1000)
      
# 		if (i+1) % (5*bat_per_epo) == 0:
# 			print(calculate_fid(1))
# # scale an array of images to a new size
def scale_images(images, new_shape):
	images_list = list()
	for image in images:
		# resize with nearest neighbor interpolation
		new_image = resize(image, new_shape, 0)
		# store
		images_list.append(new_image)
	return asarray(images_list)

# size of the latent space
latent_dim = 128
# create the discriminator
c_model = define_discriminator()
# create the generator
print('\n')
g_model = define_generator(latent_dim+10)
# create the gan
gan_model = define_gan(g_model, c_model)
# load image data
dataset_train= load_real_samples()



In [0]:
train(g_model, c_model, gan_model, dataset_train, latent_dim, 150)

Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where


/usr/local/lib/python3.6/dist-packages/keras/engine/training.py:493: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'


/usr/local/lib/python3.6/dist-packages/keras/engine/training.py:493: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'


>1, c1=-1.294, c2=0.030 g=-0.007


/usr/local/lib/python3.6/dist-packages/keras/engine/training.py:493: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'


>2, c1=-13.213, c2=1.486 g=-0.210
>3, c1=-26.486, c2=1.026 g=-0.006
>4, c1=-30.815, c2=0.261 g=-0.070
>5, c1=-36.029, c2=1.988 g=-0.368
>6, c1=-39.147, c2=6.077 g=-7.731
>7, c1=-33.836, c2=17.087 g=-16.659
>8, c1=-27.125, c2=22.766 g=-4.811
>9, c1=-43.299, c2=1.878 g=0.013
>10, c1=-56.819, c2=0.003 g=-0.009
>11, c1=-66.146, c2=0.074 g=-0.103
>12, c1=-70.261, c2=0.401 g=-0.090
>13, c1=-77.181, c2=0.513 g=-0.650
>14, c1=-78.659, c2=0.580 g=-0.444
>15, c1=-90.712, c2=1.014 g=-0.781
>16, c1=-92.749, c2=1.018 g=-1.358
>17, c1=-103.296, c2=1.707 g=-2.643
>18, c1=-109.826, c2=3.856 g=-6.713
>19, c1=-107.008, c2=7.525 g=-13.444
>20, c1=-121.023, c2=15.348 g=-29.458
>21, c1=-129.182, c2=22.082 g=-41.492
>22, c1=-130.179, c2=33.588 g=-60.113
>23, c1=-136.635, c2=60.482 g=-110.399
>24, c1=-137.485, c2=108.813 g=-180.992
>25, c1=-132.028, c2=157.490 g=-253.791
>26, c1=-120.540, c2=182.230 g=-257.033
>27, c1=-83.395, c2=136.177 g=-60.107
>28, c1=-53.806, c2=12.386 g=-0.195
>29, c1=-94.454, c2=0.025